In [2]:
import geopandas as gpd
import numpy as np
import pandas as pd
import os
import json
from pathlib import Path
import datetime
from shapely import wkt
from tqdm import tqdm

from joblib import Parallel, delayed
import multiprocessing

import trackintel as ti
from trackintel.analysis.tracking_quality import temporal_tracking_quality

In [3]:
ti.__version__

'1.2.4'

In [4]:
# read file storage
Dataset_file = os.path.join("..", "paths.json")
with open(Dataset_file) as json_file:
    CONFIG = json.load(json_file)

# Read staypoints

In [4]:
sp = pd.read_csv(os.path.join(CONFIG[f"raw_mobis"], "sps.csv"))

In [5]:
# geometry
sp["geometry"] = gpd.GeoSeries.from_wkt(sp["geometry"])
sp = gpd.GeoDataFrame(sp, crs="EPSG:4326", geometry="geometry")

In [6]:
sp["started_at"] = pd.to_datetime(sp["started_at"], format='mixed', yearfirst=True, utc=True)
sp["finished_at"] = pd.to_datetime(sp["finished_at"], format='mixed', yearfirst=True, utc=True)

In [7]:
# to trackintel
sp = ti.io.read_staypoints_gpd(sp)

In [8]:
type(sp)

trackintel.model.staypoints.Staypoints

# Read triplegs

In [9]:
# only a subset for testing
# tpls = pd.read_csv(os.path.join(CONFIG["raw_mobis"], "legs.csv"), nrows=100000)

# full
tpls = pd.read_csv(os.path.join(CONFIG["raw_mobis"], "legs.csv"), usecols=[0, 1, 3, 6])

In [10]:
# geometry
tpls["geometry"] = gpd.GeoSeries.from_wkt(tpls["geometry"])
tpls = gpd.GeoDataFrame(tpls, crs="EPSG:4326", geometry="geometry")

In [11]:
tpls["started_at"] = pd.to_datetime(tpls["started_at"], format='mixed', yearfirst=True, utc=True)
tpls["finished_at"] = pd.to_datetime(tpls["finished_at"], format='mixed', yearfirst=True, utc=True)

In [12]:
# to trackintel, filter invalid geometry
tpls = ti.io.read_triplegs_gpd(tpls[tpls.geometry.is_valid])

In [13]:
type(tpls)

trackintel.model.triplegs.Triplegs

# Final cleaning

In [14]:
tpls["user_id"].unique().shape, sp["user_id"].unique().shape

((5152,), (5130,))

In [15]:
# negative duration records have already been dropped
sp["duration"] = (sp["finished_at"] - sp["started_at"]).dt.total_seconds()
tpls["duration"] = (tpls["finished_at"] - tpls["started_at"]).dt.total_seconds()

In [16]:
sp = sp.sort_values(by="started_at").reset_index(drop=True)
tpls = tpls.sort_values(by="started_at").reset_index(drop=True)

sp.index.name = "id"
tpls.index.name = "id"

In [17]:
tpls

started_at                      finished_at  \
id                                                                          
0       2019-09-01 00:43:39.546000+00:00 2019-09-01 00:45:48.144000+00:00   
1       2019-09-01 01:02:29.142999+00:00 2019-09-01 01:04:06.545000+00:00   
2       2019-09-01 01:04:06.545000+00:00 2019-09-01 01:20:53.158999+00:00   
3       2019-09-01 02:52:34.696000+00:00 2019-09-01 02:52:57.516000+00:00   
4       2019-09-01 03:38:14.168999+00:00 2019-09-01 03:44:58.186000+00:00   
...                                  ...                              ...   
6391621        2022-12-20 23:11:12+00:00        2022-12-21 00:12:59+00:00   
6391622        2022-12-20 23:21:17+00:00        2022-12-20 23:23:22+00:00   
6391623        2022-12-21 00:14:16+00:00        2022-12-21 00:16:52+00:00   
6391624        2022-12-21 01:17:30+00:00        2022-12-21 01:33:09+00:00   
6391625        2022-12-21 01:33:10+00:00        2022-12-21 01:34:33+00:00   

                                                  geometry  user_id  \
id                                                                    
0        LINESTRING (-123.08238 44.00756, -123.08245 44...    AQXET   
1        LINESTRING (-123.08249 44.00756, -123.08265 44...    AQXET   
2        LINESTRING (-123.08280 44.00765, -123.08264 44...    AQXET   
3        LINESTRING (-73.55908 45.58575, -73.45893 45.4...    LCGZG   
4        LINESTRING (-123.10317 44.05745, -123.10339 44...    AQXET   
...                                                    ...      ...   
6391621  LINESTRING (8.30994 47.04233, 8.30994 47.04233...  LJTBXCB   
6391622  LINESTRING (8.30760 47.04887, 8.30760 47.04887...  LCITXER   
6391623  LINESTRING (8.55880 47.43092, 8.55880 47.43092...  LJTBXCB   
6391624  LINESTRING (8.55880 47.43081, 8.55880 47.43081...  LJTBXCB   
6391625  LINESTRING (8.50067 47.38768, 8.50067 47.38769...  LJTBXCB   

            duration  
id                    
0         128.598000  
1          97.402001  
2        1006.613999  
3          22.820000  
4         404.017001  
...              ...  
6391621  3707.000000  
6391622   125.000000  
6391623   156.000000  
6391624   939.000000  
6391625    83.000000  

[6391626 rows x 5 columns]

In [18]:
sp

started_at                      finished_at  \
id                                                                          
0       2019-09-01 00:45:48.144000+00:00 2019-09-01 01:02:29.142999+00:00   
1       2019-09-01 01:20:53.158999+00:00 2019-09-01 03:38:14.168999+00:00   
2       2019-09-01 02:52:57.516000+00:00 2019-09-01 18:18:04.576999+00:00   
3       2019-09-01 03:44:58.186000+00:00 2019-09-01 15:49:36.105000+00:00   
4       2019-09-01 08:46:09.986000+00:00 2019-09-01 09:05:17.973999+00:00   
...                                  ...                              ...   
4811534        2022-12-20 22:21:35+00:00        2022-12-20 22:45:11+00:00   
4811535        2022-12-20 22:31:10+00:00        2022-12-20 22:31:55+00:00   
4811536        2022-12-20 22:51:14+00:00        2022-12-20 23:11:12+00:00   
4811537        2022-12-21 00:12:59+00:00        2022-12-21 00:14:16+00:00   
4811538        2022-12-21 00:16:52+00:00        2022-12-21 01:17:30+00:00   

                            geometry  purpose detected_purpose  confidence  \
id                                                                           
0        POINT (-123.08249 44.00756)  unknown          unknown         1.0   
1        POINT (-123.10317 44.05745)  unknown          unknown         1.0   
2         POINT (-73.45860 45.45644)  unknown          unknown         1.0   
3        POINT (-123.10147 44.03391)  unknown          unknown         1.0   
4           POINT (8.86188 46.03543)  unknown          unknown         1.0   
...                              ...      ...              ...         ...   
4811534     POINT (8.31027 47.04297)     work              NaN         NaN   
4811535     POINT (7.73043 47.48689)     work              NaN         NaN   
4811536     POINT (8.30994 47.04233)     work              NaN         NaN   
4811537     POINT (8.55880 47.43092)  unknown              NaN         NaN   
4811538     POINT (8.55880 47.43081)  unknown              NaN         NaN   

         user_id  overseas  misdetected_completely      duration  
id                                                                
0          AQXET      True                   False   1000.998999  
1          AQXET      True                   False   8241.010000  
2          LCGZG      True                   False  55507.060999  
3          AQXET      True                   False  43477.919000  
4          MMOQN     False                   False   1147.987999  
...          ...       ...                     ...           ...  
4811534  LJTBXCB     False                   False   1416.000000  
4811535    YPZKQ     False                   False     45.000000  
4811536  LJTBXCB     False                   False   1198.000000  
4811537  LJTBXCB     False                   False     77.000000  
4811538  LJTBXCB     False                   False   3638.000000  

[4811539 rows x 10 columns]

# Filter duplicates

In [19]:
def _alter_diff(df):
    df.sort_values(by="started_at", inplace=True)
    df["diff"] = pd.NA
    df["st_next"] = pd.NaT

    diff = df["started_at"].iloc[1:].reset_index(drop=True) - df["finished_at"].iloc[:-1].reset_index(drop=True)
    df["diff"].iloc[:-1] = diff.dt.total_seconds()
    df["st_next"].iloc[:-1] = df["started_at"].iloc[1:].reset_index(drop=True)

    df.loc[df["diff"] < 0, "finished_at"] = df.loc[df["diff"] < 0, "st_next"]

    df["started_at"], df["finished_at"] = pd.to_datetime(df["started_at"]), pd.to_datetime(df["finished_at"])
    df["duration"] = (df["finished_at"] - df["started_at"]).dt.total_seconds()

    # print(df.loc[df["diff"] < 0])
    df.drop(columns=["diff", "st_next"], inplace=True)
    df.drop(index=df[df["duration"] <= 0].index, inplace=True)

    return df

def filter_duplicates(sp, tpls):

    # merge trips and staypoints
    sp["type"] = "sp"
    tpls["type"] = "tpl"
    df_all = pd.merge(sp, tpls, how="outer")

    df_all = df_all.groupby("user_id", as_index=False).apply(_alter_diff)
    sp = df_all.loc[df_all["type"] == "sp"].drop(columns=["type"])
    tpls = df_all.loc[df_all["type"] == "tpl"].drop(columns=["type"])

    sp = sp[["id", "user_id", "started_at", "finished_at", "geometry", "duration", "purpose", "detected_purpose", "overseas"]]
    tpls = tpls[["id", "user_id", "started_at", "finished_at","duration", "geometry"]]

    return sp.set_index("id"), tpls.set_index("id")

sp, tpls = filter_duplicates(sp.reset_index(), tpls.reset_index())

C:\Users\hong\AppData\Local\Temp\ipykernel_23752\961955421.py:8: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0     2019-11-23 22:59:06.335000+00:00
1     2019-11-23 23:10:55.311000+00:00
2     2019-11-24 12:05:12.114000+00:00
3     2019-12-02 08:56:47.605999+00:00
4     2019-12-02 09:09:49.262000+00:00
                    ...               
638   2020-02-01 10:22:17.121000+00:00
639   2020-02-01 11:26:08.611999+00:00
640   2020-02-02 03:55:30.956000+00:00
641   2020-02-02 04:03:42.694999+00:00
642   2020-02-02 13:11:06.492000+00:00
Name: started_at, Length: 643, dtype: datetime64[ns, UTC]' has dtype incompatible with datetime64[ns], please explicitly cast to a compatible dtype first.
  df["st_next"].iloc[:-1] = df["started_at"].iloc[1:].reset_index(drop=True)
C:\Users\hong\AppData\Local\Temp\ipykernel_23752\961955421.py:10: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a fut

In [22]:
len(sp)

4804194

# Read quality filter file

In [23]:
quality_path = os.path.join("..","data", "quality")
quality_file = os.path.join(quality_path, "mobis_filtered.csv")
if Path(quality_file).is_file():
    valid_users = pd.read_csv(quality_file)["user_id"].values
else:
    if not os.path.exists(quality_path):
        os.makedirs(quality_path)

In [25]:
len(valid_users)

2113

# Define activity

In [27]:
sp["is_activity"] = True

# wait is not an activity
sp.loc[sp["purpose"] == "wait", "is_activity"] = False

# shorter than 25min
sp.loc[(sp["purpose"] == "unknown") & (sp["duration"] < 25 * 60), "is_activity"] = False

In [28]:
sp["is_activity"].value_counts()

is_activity
True     3589215
False    1214979
Name: count, dtype: int64

# Generate user filter

In [23]:
# the trackintel trip generation
sp, tpls, trips = ti.preprocessing.triplegs.generate_trips(sp, tpls, gap_threshold=25, add_geometry=False)

In [27]:
sp

detected_purpose      duration                      finished_at  \
id                                                                       
823049              NaN   1232.405999 2019-11-19 10:02:35.168999+00:00   
888565              NaN  46456.803000 2019-11-24 12:05:12.114000+00:00   
986443              NaN   1048.307999 2019-12-02 09:27:17.569999+00:00   
989148              NaN   3136.263000 2019-12-02 13:41:13.334000+00:00   
989714              NaN  15386.960000 2019-12-02 17:58:06.154999+00:00   
...                 ...           ...                              ...   
576535             home   6070.152999 2019-10-31 17:07:26.619999+00:00   
578695             home   6727.276000 2019-10-31 19:02:57.200000+00:00   
580864             home  44547.902000 2019-11-01 07:45:05.378999+00:00   
584556             home   4681.997000 2019-11-01 09:09:36.236000+00:00   
587147             home  18748.664000 2019-11-01 16:19:51.618999+00:00   

                        geometry  is_activity overseas  purpose  \
id                                                                
823049  POINT (7.55245 46.84046)        False    False  unknown   
888565  POINT (7.55235 46.84037)         True    False  unknown   
986443  POINT (7.63289 46.77817)        False    False  unknown   
989148  POINT (7.63035 46.77693)         True    False  unknown   
989714  POINT (7.63270 46.77812)         True    False  unknown   
...                          ...          ...      ...      ...   
576535  POINT (8.77996 47.37271)         True    False     home   
578695  POINT (8.77844 47.37405)         True    False     home   
580864  POINT (8.77755 47.37582)         True    False     home   
584556  POINT (8.77726 47.37594)         True    False     home   
587147  POINT (8.77752 47.37578)         True    False     home   

                             started_at user_id  prev_trip_id  next_trip_id  \
id                                                                            
823049 2019-11-19 09:42:02.763000+00:00   AAALY          <NA>          <NA>   
888565 2019-11-23 23:10:55.311000+00:00   AAALY             0             1   
986443 2019-12-02 09:09:49.262000+00:00   AAALY          <NA>          <NA>   
989148 2019-12-02 12:48:57.071000+00:00   AAALY          <NA>             3   
989714 2019-12-02 13:41:39.194999+00:00   AAALY             3             4   
...                                 ...     ...           ...           ...   
576535 2019-10-31 15:26:16.467000+00:00   ZZYIC       3466351       3466352   
578695 2019-10-31 17:10:49.924000+00:00   ZZYIC       3466352          <NA>   
580864 2019-10-31 19:22:37.476999+00:00   ZZYIC          <NA>       3466353   
584556 2019-11-01 07:51:34.239000+00:00   ZZYIC       3466353       3466354   
587147 2019-11-01 11:07:22.954999+00:00   ZZYIC       3466354       3466355   

        trip_id  
id               
823049     <NA>  
888565     <NA>  
986443        2  
989148     <NA>  
989714     <NA>  
...         ...  
576535     <NA>  
578695     <NA>  
580864     <NA>  
584556     <NA>  
587147     <NA>  

[4804194 rows x 12 columns]

In [30]:
def _split_overlaps(source, granularity="day", max_iter=60):
    if granularity == "hour":
        # every split over hour splits also over day
        # this way to split of an entry over a month takes 30+24 iterations instead of 30*24.
        df = _split_overlaps(source, granularity="day", max_iter=max_iter)
    else:
        df = source.copy()

    change_flag = _get_split_index(df, granularity=granularity)
    iter_count = 0

    freq = "D" if granularity == "day" else "H"
    # Iteratively split one day/hour from multi day/hour entries until no entry spans over multiple days/hours
    while change_flag.sum() > 0:
        # calculate new finished_at timestamp (00:00 midnight)
        new_df = df.loc[change_flag].copy()
        # print(change_flag)
        # print(new_df)
        df.loc[change_flag, "finished_at"] = (df.loc[change_flag, "started_at"] + pd.Timestamp.resolution).dt.ceil(freq)

        # create new entries with remaining timestamp
        new_df["started_at"] = df.loc[change_flag, "finished_at"]

        df = pd.concat((df, new_df), ignore_index=True, sort=True)

        change_flag = _get_split_index(df, granularity=granularity)
        iter_count += 1
        if iter_count >= max_iter:
            break

    if "duration" in df.columns:
        df["duration"] = df["finished_at"] - df["started_at"]
    return df

def _get_split_index(df, granularity="day"):
    freq = "D" if granularity == "day" else "H"
    cond1 = df["started_at"].dt.floor(freq) != (df["finished_at"] - pd.Timedelta.resolution).dt.floor(freq)
    # catch corner case where both on same border and subtracting would lead to error
    cond2 = df["started_at"] != df["finished_at"]
    return cond1 & cond2
    
def _filter_user(df, min_thres, mean_thres):
    consider = df.loc[df["quality"] != 0]
    if (consider["quality"].min() > min_thres) and (consider["quality"].mean() > mean_thres):
        return df


def _get_tracking_quality(df, window_size):

    weeks = (df["finished_at"].max() - df["started_at"].min()).days // 7
    start_date = df["started_at"].min().date()

    quality_list = []
    # construct the sliding week gdf
    for i in range(0, weeks - window_size + 1):
        curr_start = datetime.datetime.combine(start_date + datetime.timedelta(weeks=i), datetime.time())
        curr_end = datetime.datetime.combine(curr_start + datetime.timedelta(weeks=window_size), datetime.time())

        # the total df for this time window
        cAll_gdf = df.loc[(df["started_at"] >= curr_start) & (df["finished_at"] < curr_end)]
        if cAll_gdf.shape[0] == 0:
            continue
        total_sec = (curr_end - curr_start).total_seconds()

        quality_list.append([i, cAll_gdf["duration"].sum() / total_sec])
    ret = pd.DataFrame(quality_list, columns=["timestep", "quality"])
    ret["user_id"] = df["user_id"].unique()[0]
    return ret

def calculate_user_quality(sp, trips, file_path, quality_filter):

    trips["started_at"] = pd.to_datetime(trips["started_at"]).dt.tz_localize(None)
    trips["finished_at"] = pd.to_datetime(trips["finished_at"]).dt.tz_localize(None)
    sp["started_at"] = pd.to_datetime(sp["started_at"]).dt.tz_localize(None)
    sp["finished_at"] = pd.to_datetime(sp["finished_at"]).dt.tz_localize(None)

    # merge trips and staypoints
    print("starting merge", sp.shape, trips.shape)
    sp["type"] = "sp"
    trips["type"] = "tpl"
    all_df = pd.concat([sp, trips])
    print("finished merge", all_df.shape)
    print("*" * 50)
    all_df = _split_overlaps(all_df, granularity="day")
    all_df["duration"] = (all_df["finished_at"] - all_df["started_at"]).dt.total_seconds()

    print(len(all_df["user_id"].unique()))

    # get quality
    total_quality = temporal_tracking_quality(all_df, granularity="all")
    # get tracking days
    total_quality["days"] = (
        all_df.groupby("user_id").apply(lambda x: (x["finished_at"].max() - x["started_at"].min()).days).values
    )
    # filter based on days
    user_filter_day = (
        total_quality.loc[(total_quality["days"] > quality_filter["day_filter"])]
        .reset_index(drop=True)["user_id"]
        .unique()
    )
    # filter based on sliding quality
    sliding_quality = (
        all_df.groupby("user_id")
        .apply(_get_tracking_quality, window_size=quality_filter["window_size"])
        .reset_index(drop=True)
    )

    filter_after_day = sliding_quality.loc[sliding_quality["user_id"].isin(user_filter_day)]

    if "min_thres" in quality_filter:
        # filter based on quanlity
        filter_after_day = (
            filter_after_day.groupby("user_id")
            .apply(_filter_user, min_thres=quality_filter["min_thres"], mean_thres=quality_filter["mean_thres"])
            .reset_index(drop=True)
            .dropna()
        )

    filter_after_user_quality = filter_after_day.groupby("user_id", as_index=False)["quality"].mean()

    print("final selected user", filter_after_user_quality.shape[0])
    filter_after_user_quality.to_csv(file_path, index=False)
    return filter_after_user_quality["user_id"].values

quality_filter = {"day_filter": 50, "window_size": 5, "min_thres": 0.5, "mean_thres": 0.6}
valid_users = calculate_user_quality(sp.copy().reset_index(), trips.copy().reset_index(), quality_file, quality_filter)

starting merge (4804194, 13) (3466356, 6)
finished merge (8270550, 16)
**************************************************
5168


C:\Users\hong\AppData\Local\Temp\ipykernel_34516\1920938679.py:103: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  all_df.groupby("user_id")


final selected user 2113


# Filter
## valid users

In [29]:
sp = sp.loc[sp["user_id"].isin(valid_users)]

In [30]:
sp["is_activity"].value_counts()

is_activity
True     1167459
False     410786
Name: count, dtype: int64

In [32]:
len(sp["user_id"].unique())

2113

## Switzerland records

In [33]:
def _filter_within_swiss(stps, swissBound):
    """Spatial filtering of staypoints."""
    # save a copy of the original projection
    init_crs = stps.crs
    # project to projected system
    stps = stps.to_crs(swissBound.crs)

    ## parallel for speeding up
    stps["within"] = _apply_parallel(stps["geometry"], _apply_extract, swissBound)
    sp_swiss = stps[stps["within"] == True].copy()
    sp_swiss.drop(columns=["within"], inplace=True)

    return sp_swiss.to_crs(init_crs)
    
def _apply_extract(df, swissBound):
    """The func for _apply_parallel: judge whether inside a shp."""
    tqdm.pandas(desc="pandas bar")
    shp = swissBound["geometry"].to_numpy()[0]
    return df.progress_apply(lambda x: shp.contains(x))


def _apply_parallel(df, func, other, n=-1):
    """parallel apply for spending up."""
    if n is None:
        n = -1
    dflength = len(df)
    cpunum = multiprocessing.cpu_count()
    if dflength < cpunum:
        spnum = dflength
    if n < 0:
        spnum = cpunum + n + 1
    else:
        spnum = n or 1

    sp = list(range(dflength)[:: int(dflength / spnum + 0.5)])
    sp.append(dflength)
    slice_gen = (slice(*idx) for idx in zip(sp[:-1], sp[1:]))
    results = Parallel(n_jobs=n, verbose=0)(delayed(func)(df.iloc[slc], other) for slc in slice_gen)
    return pd.concat(results)

swissBoundary = gpd.read_file(os.path.join("..", "data", "swiss", "swiss.shp"))

print("Before spatial filtering: ", sp.shape[0])
sp_swiss = _filter_within_swiss(sp, swissBoundary)
print("After spatial filtering: ", sp_swiss.shape[0])

Before spatial filtering:  1578245
After spatial filtering:  1460189


In [28]:
# sp_swiss = sp

# Activity staypoints

In [35]:
sp_swiss = sp_swiss.loc[sp_swiss["is_activity"] == True]

In [36]:
len(sp_swiss)

1094017

# Generate locations

In [37]:
sp_swiss, locs = sp_swiss.as_staypoints.generate_locations(
    epsilon=20, num_samples=1, distance_metric="haversine", agg_level="dataset", n_jobs=-1
)

## Filter noise staypoints

In [38]:
sp_filter = sp_swiss.loc[~sp_swiss["location_id"].isna()].copy()
print("After filter non-location staypoints: ", sp_filter.shape[0])

After filter non-location staypoints:  1094017


## Save locations

In [40]:
locs = locs[~locs.index.duplicated(keep="first")]
filtered_locs = locs.loc[locs.index.isin(sp_swiss["location_id"].unique())]

# locations without duplication, user_id have no meaning
filtered_locs.as_locations.to_csv(os.path.join("..", "data", f"loc.csv"))
print("Location size: ", sp_swiss["location_id"].unique().shape[0], filtered_locs.shape[0])

Location size:  162303 162303


## merge staypoints

In [41]:
sp_filter = sp_filter[["user_id", "started_at", "finished_at", "geometry", "location_id"]]

sp_merged = sp_filter.as_staypoints.merge_staypoints(
    triplegs=pd.DataFrame([]), max_time_gap="1min", agg={"location_id": "first", "geometry": "first"}
)
print("After staypoints merging: ", sp_merged.shape[0])

C:\ProgramData\Anaconda3\envs\generation\lib\site-packages\trackintel\preprocessing\staypoints.py:286: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  sp_tpls = pd.concat([sp_merge, tpls_merge]).sort_values(by=["user_id", "started_at"])


After staypoints merging:  1079922


In [42]:
sp_merged

user_id                       started_at  \
id                                                
295826   AAGAF 2019-10-09 11:30:34.141000+00:00   
303827   AAGAF 2019-10-10 06:14:49.141999+00:00   
304385   AAGAF 2019-10-10 07:03:24.426000+00:00   
307381   AAGAF 2019-10-10 11:10:24.605999+00:00   
316446   AAGAF 2019-10-11 06:15:49.739000+00:00   
...        ...                              ...   
576535   ZZYIC 2019-10-31 15:26:16.467000+00:00   
578695   ZZYIC 2019-10-31 17:10:49.924000+00:00   
580864   ZZYIC 2019-10-31 19:22:37.476999+00:00   
584556   ZZYIC 2019-11-01 07:51:34.239000+00:00   
587147   ZZYIC 2019-11-01 11:07:22.954999+00:00   

                            finished_at  location_id                  geometry  
id                                                                              
295826 2019-10-10 05:43:17.674999+00:00            0  POINT (7.56522 47.54562)  
303827 2019-10-10 06:53:54.841000+00:00            1  POINT (7.56376 47.54795)  
304385 2019-10-10 08:18:20.864000+00:00            2  POINT (7.58173 47.55644)  
307381 2019-10-10 13:54:34.799339+00:00            2  POINT (7.58173 47.55641)  
316446 2019-10-11 11:36:29.907000+00:00            0  POINT (7.56513 47.54571)  
...                                 ...          ...                       ...  
576535 2019-10-31 17:07:26.619999+00:00        11963  POINT (8.77996 47.37271)  
578695 2019-10-31 19:02:57.200000+00:00       162302  POINT (8.77844 47.37405)  
580864 2019-11-01 07:45:05.378999+00:00       162235  POINT (8.77755 47.37582)  
584556 2019-11-01 09:09:36.236000+00:00       162235  POINT (8.77726 47.37594)  
587147 2019-11-01 16:19:51.618999+00:00       162235  POINT (8.77752 47.37578)  

[1079922 rows x 5 columns]

# Calculate staypoint duration and activity duration

In [95]:
sp_merged.sort_values(by=["user_id", "started_at"], inplace=True)

sp_merged["duration"] = (sp_merged["finished_at"] - sp_merged["started_at"]).dt.total_seconds() // 60

In [96]:
def get_act_duration(df):
    df["act_duration"] = pd.NA
    df["act_duration"] = (df["finished_at"].shift(-1) - df["finished_at"]).dt.total_seconds().shift(1)// 60
    
    df["act_duration"].iloc[0] = df["duration"].iloc[0]

    return df["act_duration"]

sp_merged["act_duration"] = sp_merged.groupby("user_id").apply(get_act_duration).values

In [97]:
sp_merged

user_id                       started_at  \
id                                                
295826   AAGAF 2019-10-09 11:30:34.141000+00:00   
303827   AAGAF 2019-10-10 06:14:49.141999+00:00   
304385   AAGAF 2019-10-10 07:03:24.426000+00:00   
307381   AAGAF 2019-10-10 11:10:24.605999+00:00   
316446   AAGAF 2019-10-11 06:15:49.739000+00:00   
...        ...                              ...   
576535   ZZYIC 2019-10-31 15:26:16.467000+00:00   
578695   ZZYIC 2019-10-31 17:10:49.924000+00:00   
580864   ZZYIC 2019-10-31 19:22:37.476999+00:00   
584556   ZZYIC 2019-11-01 07:51:34.239000+00:00   
587147   ZZYIC 2019-11-01 11:07:22.954999+00:00   

                            finished_at  location_id  \
id                                                     
295826 2019-10-10 05:43:17.674999+00:00            0   
303827 2019-10-10 06:53:54.841000+00:00            1   
304385 2019-10-10 08:18:20.864000+00:00            2   
307381 2019-10-10 13:54:34.799339+00:00            2   
316446 2019-10-11 11:36:29.907000+00:00            0   
...                                 ...          ...   
576535 2019-10-31 17:07:26.619999+00:00        11963   
578695 2019-10-31 19:02:57.200000+00:00       162302   
580864 2019-11-01 07:45:05.378999+00:00       162235   
584556 2019-11-01 09:09:36.236000+00:00       162235   
587147 2019-11-01 16:19:51.618999+00:00       162235   

                        geometry  duration  act_duration  
id                                                        
295826  POINT (7.56522 47.54562)    1092.0        1092.0  
303827  POINT (7.56376 47.54795)      39.0          70.0  
304385  POINT (7.58173 47.55644)      74.0          84.0  
307381  POINT (7.58173 47.55641)     164.0         336.0  
316446  POINT (7.56513 47.54571)     320.0        1301.0  
...                          ...       ...           ...  
576535  POINT (8.77996 47.37271)     101.0         182.0  
578695  POINT (8.77844 47.37405)     112.0         115.0  
580864  POINT (8.77755 47.37582)     742.0         762.0  
584556  POINT (8.77726 47.37594)      78.0          84.0  
587147  POINT (8.77752 47.37578)     312.0         430.0  

[1079922 rows x 7 columns]

# Validate and save

In [98]:
print("User size: ", len(sp_merged["user_id"].unique()))

User size:  2112


In [99]:
sp_merged.to_csv(os.path.join("..", "data", f"sp_all.csv"))

# Generate small dataset

In [5]:
sp = pd.read_csv(os.path.join("..", "data", f"sp_all.csv"), index_col="id")

sp

user_id                        started_at  \
id                                                 
295826   AAGAF  2019-10-09 11:30:34.141000+00:00   
303827   AAGAF  2019-10-10 06:14:49.141999+00:00   
304385   AAGAF  2019-10-10 07:03:24.426000+00:00   
307381   AAGAF  2019-10-10 11:10:24.605999+00:00   
316446   AAGAF  2019-10-11 06:15:49.739000+00:00   
...        ...                               ...   
576535   ZZYIC  2019-10-31 15:26:16.467000+00:00   
578695   ZZYIC  2019-10-31 17:10:49.924000+00:00   
580864   ZZYIC  2019-10-31 19:22:37.476999+00:00   
584556   ZZYIC  2019-11-01 07:51:34.239000+00:00   
587147   ZZYIC  2019-11-01 11:07:22.954999+00:00   

                             finished_at  location_id  \
id                                                      
295826  2019-10-10 05:43:17.674999+00:00            0   
303827  2019-10-10 06:53:54.841000+00:00            1   
304385  2019-10-10 08:18:20.864000+00:00            2   
307381  2019-10-10 13:54:34.799339+00:00            2   
316446  2019-10-11 11:36:29.907000+00:00            0   
...                                  ...          ...   
576535  2019-10-31 17:07:26.619999+00:00        11963   
578695  2019-10-31 19:02:57.200000+00:00       162302   
580864  2019-11-01 07:45:05.378999+00:00       162235   
584556  2019-11-01 09:09:36.236000+00:00       162235   
587147  2019-11-01 16:19:51.618999+00:00       162235   

                                            geometry  duration  act_duration  
id                                                                            
295826  POINT (7.565219252705515 47.545616383391014)    1092.0        1092.0  
303827   POINT (7.563759803278834 47.54794768304769)      39.0          70.0  
304385    POINT (7.581727914351441 47.5564374119498)      74.0          84.0  
307381   POINT (7.581729846308135 47.55641482529889)     164.0         336.0  
316446   POINT (7.565127647736598 47.54571219157556)     320.0        1301.0  
...                                              ...       ...           ...  
576535   POINT (8.779955508622193 47.37271491009289)     101.0         182.0  
578695   POINT (8.778435090438501 47.37405248736652)     112.0         115.0  
580864  POINT (8.777547641952243 47.375817643427915)     742.0         762.0  
584556   POINT (8.77725754861859 47.375938470094724)      78.0          84.0  
587147    POINT (8.77752030861889 47.37578288152317)     312.0         430.0  

[1079922 rows x 7 columns]

In [6]:
np.random.seed(0)

selected_user = np.random.choice(sp["user_id"].unique(), 50, replace=False)
selected_user

array(['VZZAM', 'NSEWU', 'SDAJB', 'LCGQUCB', 'LZIMGWA', 'IHWEP', 'MPZFJ',
       'LVFRPHG', 'HGMAP', 'CLMUT', 'BDVLG', 'HSUHS', 'LITFYCJ',
       'LNGQHDJ', 'LNNJEVU', 'PHPOM', 'QKXSO', 'DGSPE', 'GJZXR',
       'LMLANBV', 'WOFJG', 'HQZVG', 'DTVCR', 'PVSHL', 'ZWWMG', 'DSPHZ',
       'BFCVL', 'RWBCM', 'RYXZB', 'LFJMGHT', 'RKHPL', 'SRYVJ', 'LGFRVXC',
       'LQSZMTA', 'NCCNT', 'XIBZX', 'NOSKP', 'LSXGDJC', 'LDHQVGB',
       'VMOGN', 'XRZPJ', 'DTTTZ', 'SLCTX', 'MPLLT', 'DBHIN', 'LLUBDNN',
       'MUMYH', 'OVAPK', 'UZRPW', 'LPJJH'], dtype=object)

In [7]:
sp.loc[sp["user_id"].isin(selected_user)].to_csv(os.path.join("..", "data", f"sp_tiny.csv"))

# Generate all visited location dataset

In [4]:
import sys
sys.path.insert(1, os.path.join(sys.path[0], '..'))

from utils.utils import load_data

In [5]:
sp = pd.read_csv(os.path.join("..", "data", "sp_all.csv"), index_col="id")
loc = pd.read_csv(os.path.join("..", "data", "loc_s2_level10_13.csv"), index_col="id")

In [6]:
sp = load_data(sp, loc)

In [7]:
sp["level"].value_counts()

level
13    1078360
12       1283
11        256
10         23
Name: count, dtype: int64

In [8]:
len(sp["location_id"].unique())

14881

In [9]:
s2_loc = pd.read_csv(os.path.join("..", "data", "s2_loc_all_level10_13.csv"), index_col="id")

visited_loc = s2_loc.loc[s2_loc["loc_id"].isin(sp["location_id"].unique())].copy()

# final clearning
visited_loc.index = np.arange(len(visited_loc))
visited_loc.index.name = "id"

In [10]:
len(visited_loc)

14881

In [11]:
visited_loc.to_csv(os.path.join("..", "data", "s2_loc_visited_level10_13.csv"))